# Natural Convection with SpatialPy

## Definition of the model

### Imports and definitions

In [1]:
import os
import sys
import math
sys.path.insert(1, "../..")
import numpy as np
import matplotlib.pyplot as plt

import spatialpy

In [2]:
class Cylinder(spatialpy.Geometry):
    def __init__(self, radius):
        self.radius = radius
    
    def inside(self, x, on_boundary):
        return x[0]**2 + x[1]**2 < self.radius**2

In [3]:
class Walls(spatialpy.Geometry):
    def __init__(self, minint, maxint):
        self.min = minint
        self.max = maxint
    
    def inside(self, x, on_boundary):
        # Bottom Wall
        if x[1] <= self.min: return True
        # Top Wall
        if x[1] >= self.max: return True
        # Left Wall
        if x[0] <= self.min: return True
        # Right Wall
        if x[0] >= self.max: return True
        return False

### Model

In [14]:
class NaturalConvection(spatialpy.Model):
    FLUID = 1
    WALLS = 2
    CYLINDER = 3
    
    def __init__(self, model_name="Natural Convection", Ra=1e4):
        spatialpy.Model.__init__(self, model_name)
        
        # System Constants
        Sc = 0.7 # Schmidt Number
        kappastar = 1/math.sqrt(Sc*Ra)
        Lint = 1
        Nint = 200
        Nwall = 3
        mustar = math.sqrt(Sc/Ra)
        rho0 = 1
        c0 = 5
        radius_external = 0.1
        gravity = [0, -1, 0]
        C0 = 1.0

        # Species
        A = spatialpy.Species(name="A", diffusion_coefficient=kappastar)
        self.add_species(A)
        
        # Discretization
        Npx = Npy = Nint+2*Nwall
        Np = Npx*Npy
        
        # Compute domain bounds (including the boundary)
        delta = Lint/Nint
        L = Lint+Nwall*2*delta
        xmin = ymin = -L/2
        xmax = ymax = L/2
        minint = -Lint/2
        maxint = Lint/2
        
        # Compute volume and mass per particle
        vtot = L**2
        mi = vtot/Np # mass per particle
        
        # Domain
        e = 1e-6
        h = hc = 2.5*delta
        
        ###################################################
        # g = -1                                          #
        # Cref = 0.0                                      #
        #                                                 #
        # P0 = rho0 * v0**2                               #
        #    = rho0 * math.sqrt(g * beta * L *deltaC)**2  #
        #    = rho0 * g * beta * L * deltaC               #
        #    = rho0 * g * beta * L * (C - Cref)           #
        ###################################################
        
        domain = spatialpy.Domain.create_2D_domain(
            xlim=(xmin, xmax), ylim=(ymin, ymax), nx=Npx, ny=Npy, type_id=self.FLUID,
            mass=mi, nu=mustar, rho0=rho0, c0=c0, gravity=gravity, fixed=False
        )
        domain.dimensions = 2
        self.add_domain(domain)
        
        # Types
        self.set_type(Walls(minint, maxint), self.WALLS, fixed=True)
        self.set_type(Cylinder(radius_external), self.CYLINDER, fixed=True)
        
        # Static Domain
        self.staticDomain = False not in self.domain.fixed
        
        # Initial Conditions
        uniform_ic = spatialpy.UniformInitialCondition(A, C0, [self.CYLINDER])
        self.add_initial_condition(uniform_ic)
        
        # Boundary Conditions
        walls_bc = spatialpy.BoundaryCondition(type_id=self.WALLS, species="A", value=0, model=self)
        self.add_boundary_condition(walls_bc)
        
        cylinder_bc = spatialpy.BoundaryCondition(type_id=self.CYLINDER, species="A", value=C0, model=self)
        self.add_boundary_condition(cylinder_bc)
        
        # Timespan
        dt = 1e-4
        # nt = 10000000
        nt = 10000
        freq_results = 100
        self.timespan(np.arange(0, nt*dt+dt, freq_results*dt), timestep_size=dt)
        print(f"tspan: np.arange(0, {nt*dt+dt}, {freq_results*dt}), timestep_size: {dt}")
        self.domain.plot_types()

In [15]:
model = NaturalConvection()

tspan: np.arange(0, 1.0001, 0.01), timestep_size: 0.0001


In [ ]:
solver = spatialpy.Solver(model=model)
%time solver.compile(debug=True)

In [ ]:
%time results = solver.run(debug=True)

In [ ]:
results.plot_property("v", t_ndx=4, use_matplotlib=True)

In [ ]:
t_val = results.get_timespan()[-1]
results.plot_property("v", t_val=t_val, use_matplotlib=True)

In [ ]:
results.plot_property("type", use_matplotlib=True)